In [1]:
import json

from tqdm import tqdm
from datasets import Dataset,  DatasetDict
import sys
from rdkit import Chem

sys.path.append('C:\Program Files\RevvitySignalsSoftware\ChemDrawApplications\ChemScript\Lib')

from ChemScript import *

template = '''Using {reactants} to produce {products}, please predict the condition, including solvent and agent in SMILES notation in json format like:
'''

example = '''
```JSON
{
    "solvent": [
        "CCN(CC)CC",
        "CCOC(C)=O"
    ],
    "agent": [
        "On1nnc2ccccc21",
        "C(=NC1CCCCC1)=NC1CCCCC1",
        "Cl"
    ]
}
```
'''

orig_names = json.load(open('D:\workspace\extract_config.json', 'r'))['manual_replacements_dict']
orig_names = {v: k for k, v in orig_names.items()}

print(orig_names)

def call_chemdraw(smile):

    try:
        # 检查 SMILES 是否有效
        if not smile or not Chem.MolFromSmiles(smile):
            return smile # 如果无效，返回原始 SMILES
        smile = Chem.CanonSmiles(smile)
        m = StructureData.LoadData(smile)

        return m.ChemicalName()
    
    except Exception as e:
        print(f"Error processing SMILES {smile}: {e}")

    return smile # 如果出错，返回原始 SMILES

caches = {}
def to_iupac(smile):
    if smile in caches:
        return caches[smile]
    if smile in orig_names:
        caches[smile] = orig_names[smile]
    else:
        caches[smile] = call_chemdraw(smile)
    return caches[smile]

def list_to_iupac(smile_list):
    try:
     return [to_iupac(smile) for smile in smile_list]
    except Exception as e:
     print(f"Error in list_to_iupac: {e}")
    return smile_list

outputs = []

datas = json.load(open('D:\workspace\orderly_cleaned_train_unify.json', 'r'))
for line in tqdm(datas):
    data = {}
    data['problem'] = template.format(reactants=', '.join(list_to_iupac(line['reactant'])), products=', '.join(list_to_iupac(line['product']))) + example
    line.pop('reactant')
    line.pop('product')
    line.pop('time')
    line.pop('temperature')
    # line['solvent'] = list_to_iupac(line['solvent'])
    # line['agent'] = list_to_iupac(line['agent'])
    data['answer'] = json.dumps(line)
    outputs.append(data)

json.dump(outputs, open('D:\workspace\orderly_qa.json', 'w'))

######################################################

test_outputs = []

datas = json.load(open('D:\workspace\orderly_cleaned_test_unify.json', 'r'))
for line in tqdm(datas):
    data = {}
    data['problem'] = template.format(reactants=', '.join(list_to_iupac(line['reactant'])), products=', '.join(list_to_iupac(line['product']))) + example
    line.pop('reactant')
    line.pop('product')
    line.pop('time')
    line.pop('temperature')
    # line['solvent'] = list_to_iupac(line['solvent'])
    # line['agent'] = list_to_iupac(line['agent'])
    data['answer'] = json.dumps(line)
    test_outputs.append(data)

json.dump(test_outputs, open('D:\workspace\orderly_qa_test.json', 'w'))




----------------------------------------------------------------------------
Welcome to ChemScript/Python (23.0.1.10 February 6, 2024)
Copyright (c) 2005-2024 Revvity Signals Software, Inc.  All rights reserved.
----------------------------------------------------------------------------
For help: use the "help()" command.  For example, type: "help(StructureData)".

{'CC(C)(C)c1ccccc1': 'tert-butylbenzene', 'C1=CCCC=CCC1': '1,5-cyclooctadiene', 'CC1(C)OCC(CO)O1': '(2,2-dimethyl-1,3-dioxolan-4-yl)methanol', 'CC=CC=CC': 'trans,trans-2,4-hexadiene', 'ClCc1ccccc1': 'benzyl chloride', 'ClCC1CO1': '1-chloro-2,3-epoxypropane', 'ClC(Cl)c1ccccc1': '(dichloromethyl)benzene', 'ClC=CCl': 'trans-1,2-dichloroethene', 'C=CC=CC': '1-trans-3-pentadiene', 'CC=CC#N': '(e)-2-butenenitrile', 'ClC(Cl)(Cl)c1ccccc1': '(trichloromethyl)benzene', 'FC(F)(F)Oc1ccccc1': 'trifluoromethylphenyl ether', 'CCC=CCC': 'cis-3-hexene', 'c1ccc(CCc2ccccc2)cc1': '1,2-diphenylethane', 'CCOCCOCCOCC': 'diethyleneglycol diethyl 

  0%|                                                                            | 39/322976 [00:00<1:03:02, 85.38it/s]

Error processing SMILES NC(=O)C1=CN([C@@H]2O[C@H](COP(=O)(O)OP(=O)(O)OC[C@H]3O[C@@H](n4cnc5c(N)ncnc54)[C@H](OP(=O)(O)O)[C@@H]3O)[C@@H](O)[C@H]2O)C=CC1: Failure: "Unable to name multiply esterified polynuclear acids; failed" in GetName()


  0%|                                                                           | 202/322976 [00:02<1:13:38, 73.05it/s]

Error processing SMILES [S-][S-]: Failure: "Unsupported charge; failed" in GetName()


...

 99%|██████████████████████████████████████████████████████████████████████████▍| 33673/33930 [03:55<00:01, 179.35it/s]

Error processing SMILES CNC(=O)NC(=O)N(C1CCCCC1)C1CCCCC1: Failure: "Unable to get special locants for this amide; failed" in GetName()


100%|██████████████████████████████████████████████████████████████████████████▋| 33765/33930 [03:56<00:00, 169.17it/s]

Error processing SMILES CCN(CC)C(=S)[SH-]C: Failure: "Unsupported charge; failed" in GetName()


100%|███████████████████████████████████████████████████████████████████████████| 33930/33930 [03:57<00:00, 142.96it/s]
